In [123]:
from __future__ import (absolute_import, division, print_function,
                        unicode_literals)

import datetime  # For datetime objects
import os.path  # To manage paths
import sys  # To find out the script name (in argv[0])

# Import the backtrader platform
import backtrader as bt
import pandas as pd
import numpy as np
import pickle

In [52]:
def moving_average(x, w):
        moving_avg = np.convolve(x, np.ones(w), 'valid') / w
        padding = np.full_like(np.empty(w), np.nan)
        return np.insert(moving_avg, 0, padding)

def moving_avg_diff(short, long):
        return (short - long) / long


def get_X_y(df, binary_output=True):
    
    min_period = 24*31 + 1
    
    percent_change = (df["Close"] - df["Close"].shift(1)) / df["Close"].shift(1)
    print(percent_change[:5])

    y = percent_change.copy()
    
    print(len(y))
    
    ## TEMP
    if binary_output == True:
        y = np.zeros(percent_change.shape)
        y[np.where(percent_change > 0)] = 1
    else:
        y = y.to_numpy()
    
    print(type(y))

    moving_average_1_hours = moving_average(df["Close"], 1)
    moving_average_2_hours = moving_average(df["Close"], 2)
    moving_average_3_hours = moving_average(df["Close"], 3)
    moving_average_12_hours = moving_average(df["Close"], 12)
    moving_average_24_hours = moving_average(df["Close"], 24)
    moving_average_48_hours = moving_average(df["Close"], 48)
    moving_average_1_week = moving_average(df["Close"], 24*7)
    moving_average_1_month = moving_average(df["Close"], 24*31)
    
    print(len(moving_average_1_month))
    
    mv_1h_2h = moving_avg_diff(moving_average_1_hours, moving_average_2_hours)
    mv_1h_3h = moving_avg_diff(moving_average_1_hours, moving_average_3_hours)
    mv_3h_12h = moving_avg_diff(moving_average_3_hours, moving_average_12_hours)
    mv_12h_24h = moving_avg_diff(moving_average_12_hours, moving_average_24_hours)
    mv_24h_48h = moving_avg_diff(moving_average_24_hours, moving_average_48_hours)
    mv_48h_1w = moving_avg_diff(moving_average_48_hours, moving_average_1_week)
    mv_1w_1m = moving_avg_diff(moving_average_1_week, moving_average_1_month)
    
    print(len(mv_1w_1m))
    
    X = np.stack((mv_1h_2h, mv_1h_3h, mv_3h_12h, mv_12h_24h, mv_24h_48h, mv_48h_1w, mv_1w_1m), axis=1)
    X = X[min_period:len(X)-1]
    y = y[min_period:]
    
    print(len(X), len(y))
    
    return (X, y)

In [56]:
df = pd.read_csv("../../data/clean/bitcoin_prices.csv")

df["Time"] = pd.to_datetime(df['Time'],unit='s')
df.set_index(pd.DatetimeIndex(df['Time']), inplace=True, drop=True)
start_date = datetime.datetime(2015,7,1)
df = df[df["Time"] > start_date]

offset = 24*31 + 1 # TODO: Refactor to output ox get_features
X, y = get_X_y(df)
df = df[offset:]
for i in range(0, len(X[0,:])):
    df["X_" + str(i)] = X[:,i]
df.describe()
print(df.columns)

Time
2015-07-20 21:00:00         NaN
2015-07-20 22:00:00    0.000504
2015-07-20 23:00:00    0.006687
2015-07-21 00:00:00    0.003179
2015-07-21 01:00:00   -0.001887
Name: Close, dtype: float64
47698
<class 'numpy.ndarray'>
47699
47699
46953 46953
Index(['Unnamed: 0', 'Time', 'Low', 'High', 'Open', 'Close', 'Volume', 'X_0',
       'X_1', 'X_2', 'X_3', 'X_4', 'X_5', 'X_6'],
      dtype='object')


In [48]:
class CommInfoFractional(bt.CommissionInfo):
    def getsize(self, price, cash):
        '''Returns fractional size for cash operation @price'''
        return self.p.leverage * (cash / price)

In [49]:
if __name__ == '__main__':
    # Create a cerebro entity
    cerebro = bt.Cerebro()

    data = bt.feeds.PandasData(dataname=df)
    
    # Add the Data Feed to Cerebro
    cerebro.adddata(data)

    # Set our desired cash start
    cerebro.broker.setcash(10000.0)

    # Print out the starting conditions
    print('Starting Portfolio Value: %.2f' % cerebro.broker.getvalue())

    # Run over everything
    cerebro.run()

    # Print out the final result
    print('Final Portfolio Value: %.2f' % cerebro.broker.getvalue())

Starting Portfolio Value: 100000.00
Final Portfolio Value: 100000.00


In [138]:
# Create a Stratey
class NNStrategy(bt.Strategy):

    def log(self, txt, dt=None):
        ''' Logging function fot this strategy'''
        dt = dt or self.datas[0].datetime.date(0)
        print('%s, %s' % (dt.isoformat(), txt))

    def __init__(self):
        self.dataclose = self.datas[0].close
        self.X_0 = self.datas[0].X_0
        self.X_1 = self.datas[0].X_1
        self.X_2 = self.datas[0].X_2
        self.X_3 = self.datas[0].X_3
        self.X_4 = self.datas[0].X_4
        self.X_5 = self.datas[0].X_5
        self.X_6 = self.datas[0].X_6

        # To keep track of pending orders and buy price/commission
        self.order = None
        self.buyprice = None
        self.buycomm = None
        
        filename = "../../models/pickles/svm_binary_classifier"
        self.clf = pickle.load(open(filename, 'rb'))

    def notify_order(self, order):
        if order.status in [order.Submitted, order.Accepted]:
            # Buy/Sell order submitted/accepted to/by broker - Nothing to do
            return

        # Check if an order has been completed
        # Attention: broker could reject order if not enough cash
        if order.status in [order.Completed]:
            if order.isbuy():
                self.log(
                    'BUY EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f' %
                    (order.executed.price,
                     order.executed.value,
                     order.executed.comm))

                self.buyprice = order.executed.price
                self.buycomm = order.executed.comm
            else:  # Sell
                self.log('SELL EXECUTED, Price: %.2f, Cost: %.2f, Comm %.2f' %
                         (order.executed.price,
                          order.executed.value,
                          order.executed.comm))

            self.bar_executed = len(self)

        elif order.status in [order.Canceled, order.Margin, order.Rejected]:
            self.log('Order Canceled/Margin/Rejected')

        self.order = None

    def notify_trade(self, trade):
        if not trade.isclosed:
            return

        self.log('OPERATION PROFIT, GROSS %.2f, NET %.2f' %
                 (trade.pnl, trade.pnlcomm))

    def next(self):
        # Simply log the closing price of the series from the reference
        self.log('Close, %.2f' % self.dataclose[0])

        # Check if an order is pending ... if yes, we cannot send a 2nd one
        if self.order:
            return
    
        X = [[self.X_0[0], self.X_1[0], self.X_2[0], self.X_3[0], self.X_4[0], self.X_5[0], self.X_6[0]]]
        pred = self.clf.predict(X)[0]
        print(pred)
        if not self.position:
            if pred == 1:
                self.log('BUY CREATE, %.2f' % self.dataclose[0])
                
                # Cancel existing orders 
                self.broker.cancel(self.order)
                
                cash = self.broker.get_cash()
                limit_price = self.data.close[0] * 1.005
                size = cash * 0.95 / limit_price
                print(cash, self.data.close[0], limit_price, size)
                
                # Keep track of the created order to avoid a 2nd order
                self.order = self.buy()
                self.buy(exectype=bt.Order.Limit, size=size)
        elif self.position and pred == 0:
            
            ## TODO: figure out why it never sells all it's position
            self.log('SELL CREATE, %.2f' % self.dataclose[0])
            size = self.broker.get_value() / self.dataclose[0]
            self.sell(size=self.position.size)


class PandasData(bt.feeds.PandasData):
    params = (
        ('X_0', 'X_0'),
        ('X_1', 'X_1'),
        ('X_2', 'X_2'),
        ('X_3', 'X_3'),
        ('X_4', 'X_4'),
        ('X_5', 'X_5'),
        ('X_6', 'X_6'),
    )
    lines = ('X_0','X_1', 'X_2', 'X_3', 'X_4', 'X_5', 'X_6')

if __name__ == '__main__':
    # Create a cerebro entity
    cerebro = bt.Cerebro()

    # Add a strategy
    cerebro.addstrategy(NNStrategy)

    data = PandasData(dataname=df)
    cerebro.adddata(data)

    cerebro.broker.setcash(10000)

    # Add a FixedSize sizer according to the stake
    cerebro.addsizer(bt.sizers.FixedSize, stake=1)

    # Set the commission
    cerebro.broker.setcommission(commission=0.0)
    cerebro.broker.addcommissioninfo(CommInfoFractional())

    print('Starting Portfolio Value: %.2f' % cerebro.broker.getvalue())

    cerebro.run()

    print('Final Portfolio Value: %.2f' % cerebro.broker.getvalue())

Starting Portfolio Value: 10000.00
2015-08-20, Close, 236.60
0.0
2015-08-20, Close, 235.56
0.0
2015-08-21, Close, 235.76
1.0
2015-08-21, BUY CREATE, 235.76
10000.0 235.76 236.93879999999996 40.094741764540046
2015-08-21, BUY EXECUTED, Price: 235.75, Cost: 235.75, Comm 0.00
2015-08-21, BUY EXECUTED, Price: 235.75, Cost: 9452.34, Comm 0.00
2015-08-21, Close, 234.04
0.0
2015-08-21, SELL CREATE, 234.04
2015-08-21, SELL EXECUTED, Price: 234.05, Cost: 9688.09, Comm 0.00
2015-08-21, OPERATION PROFIT, GROSS -69.86, NET -69.86
2015-08-21, Close, 233.85
1.0
2015-08-21, BUY CREATE, 233.85
9930.13893900028 233.85 235.01924999999997 40.139826810145415
2015-08-21, BUY EXECUTED, Price: 233.88, Cost: 233.88, Comm 0.00
2015-08-21, BUY EXECUTED, Price: 233.85, Cost: 9386.70, Comm 0.00
2015-08-21, Close, 236.07
1.0
2015-08-21, Close, 235.27
0.0
2015-08-21, SELL CREATE, 235.27
2015-08-21, SELL EXECUTED, Price: 235.27, Cost: 9620.58, Comm 0.00
2015-08-21, OPERATION PROFIT, GROSS 58.39, NET 58.39
2015-08-21

0.0
2015-09-02, SELL CREATE, 229.56
2015-09-02, SELL EXECUTED, Price: 229.56, Cost: 9938.80, Comm 0.00
2015-09-02, OPERATION PROFIT, GROSS 42.60, NET 42.60
2015-09-02, Close, 230.00
0.0
2015-09-02, Close, 231.15
0.0
2015-09-02, Close, 230.43
0.0
2015-09-02, Close, 229.00
1.0
2015-09-02, BUY CREATE, 229.00
10314.983982183825 229.0 230.14499999999998 42.578525638508914
2015-09-02, BUY EXECUTED, Price: 229.13, Cost: 229.13, Comm 0.00
2015-09-02, Close, 229.68
1.0
2015-09-02, Close, 229.30
1.0
2015-09-02, Close, 229.18
1.0
2015-09-02, Close, 229.97
1.0
2015-09-03, Close, 230.20
0.0
2015-09-03, SELL CREATE, 230.20
2015-09-03, SELL EXECUTED, Price: 230.20, Cost: 229.13, Comm 0.00
2015-09-03, OPERATION PROFIT, GROSS 1.07, NET 1.07
2015-09-03, Close, 230.50
0.0
2015-09-03, Close, 229.65
0.0
2015-09-03, Close, 229.51
1.0
2015-09-03, BUY CREATE, 229.51
10316.053982183827 229.51 230.65754999999996 42.48831778138039
2015-09-03, BUY EXECUTED, Price: 229.51, Cost: 229.51, Comm 0.00
2015-09-03, BUY E

2015-09-07, BUY EXECUTED, Price: 241.35, Cost: 10201.36, Comm 0.00
2015-09-07, Close, 240.41
0.0
2015-09-07, SELL CREATE, 240.41
2015-09-07, SELL EXECUTED, Price: 240.95, Cost: 10442.71, Comm 0.00
2015-09-07, OPERATION PROFIT, GROSS -17.31, NET -17.31
2015-09-07, Close, 241.25
1.0
2015-09-07, BUY CREATE, 241.25
10775.108130898267 241.25 242.45624999999998 42.219380710348176
2015-09-07, BUY EXECUTED, Price: 241.24, Cost: 241.24, Comm 0.00
2015-09-07, BUY EXECUTED, Price: 241.24, Cost: 10185.00, Comm 0.00
2015-09-07, Close, 240.79
0.0
2015-09-07, SELL CREATE, 240.79
2015-09-07, SELL EXECUTED, Price: 240.78, Cost: 10426.24, Comm 0.00
2015-09-07, OPERATION PROFIT, GROSS -19.88, NET -19.88
2015-09-07, Close, 240.54
1.0
2015-09-07, BUY CREATE, 240.54
10755.227215771507 240.54 241.74269999999996 42.265871337512706
2015-09-07, BUY EXECUTED, Price: 240.58, Cost: 240.58, Comm 0.00
2015-09-07, BUY EXECUTED, Price: 240.54, Cost: 10166.63, Comm 0.00
2015-09-07, Close, 241.17
1.0
2015-09-07, Close, 

2015-09-18, BUY EXECUTED, Price: 232.08, Cost: 232.08, Comm 0.00
2015-09-18, BUY EXECUTED, Price: 232.08, Cost: 10123.27, Comm 0.00
2015-09-18, Close, 231.75
1.0
2015-09-18, Close, 232.52
1.0
2015-09-18, Close, 233.08
0.0
2015-09-18, SELL CREATE, 233.08
2015-09-18, SELL EXECUTED, Price: 233.08, Cost: 10355.35, Comm 0.00
2015-09-18, OPERATION PROFIT, GROSS 44.62, NET 44.62
2015-09-18, Close, 233.40
0.0
2015-09-18, Close, 233.41
0.0
2015-09-18, Close, 233.40
0.0
2015-09-18, Close, 233.75
0.0
2015-09-18, Close, 233.95
0.0
2015-09-18, Close, 233.79
0.0
2015-09-18, Close, 233.76
0.0
2015-09-18, Close, 233.47
0.0
2015-09-18, Close, 233.78
1.0
2015-09-18, BUY CREATE, 233.78
10757.203784073923 233.78 234.94889999999998 43.496026560968055
2015-09-19, BUY EXECUTED, Price: 233.78, Cost: 233.78, Comm 0.00
2015-09-19, BUY EXECUTED, Price: 233.78, Cost: 10168.50, Comm 0.00
2015-09-19, Close, 234.12
0.0
2015-09-19, SELL CREATE, 234.12
2015-09-19, SELL EXECUTED, Price: 234.12, Cost: 10402.28, Comm 0.0

2015-09-25, Close, 236.62
1.0
2015-09-25, Close, 236.20
1.0
2015-09-25, Close, 235.11
1.0
2015-09-25, Close, 235.38
1.0
2015-09-25, Close, 235.74
1.0
2015-09-25, Close, 235.89
0.0
2015-09-25, SELL CREATE, 235.89
2015-09-26, SELL EXECUTED, Price: 235.88, Cost: 10702.36, Comm 0.00
2015-09-26, OPERATION PROFIT, GROSS -44.28, NET -44.28
2015-09-26, Close, 236.00
0.0
2015-09-26, Close, 235.79
0.0
2015-09-26, Close, 236.07
1.0
2015-09-26, BUY CREATE, 236.07
11028.051168511443 236.07 237.25034999999997 44.15862235855868
2015-09-26, BUY EXECUTED, Price: 236.06, Cost: 236.06, Comm 0.00
2015-09-26, BUY EXECUTED, Price: 236.06, Cost: 10424.08, Comm 0.00
2015-09-26, Close, 236.03
0.0
2015-09-26, SELL CREATE, 236.03
2015-09-26, SELL EXECUTED, Price: 236.03, Cost: 10660.14, Comm 0.00
2015-09-26, OPERATION PROFIT, GROSS -1.35, NET -1.35
2015-09-26, Close, 234.56
0.0
2015-09-26, Close, 234.57
1.0
2015-09-26, BUY CREATE, 234.57
11026.696409840686 234.57 235.74284999999998 44.43554317489863
2015-09-26, 

...

2020-11-15, BUY EXECUTED, Price: 15998.38, Cost: 15998.38, Comm 0.00
2020-11-15, BUY EXECUTED, Price: 15998.38, Cost: 2155385.36, Comm 0.00
2020-11-15, Close, 15998.75
1.0
2020-11-15, Close, 15946.09
1.0
2020-11-15, Close, 15949.05
1.0
2020-11-15, Close, 16033.32
1.0
2020-11-15, Close, 16069.26
1.0
2020-11-15, Close, 16045.93
1.0
2020-11-15, Close, 16135.46
1.0
2020-11-15, Close, 16082.41
1.0
2020-11-15, Close, 16007.41
1.0
2020-11-15, Close, 15972.08
1.0
2020-11-15, Close, 15993.78
1.0
2020-11-15, Close, 16062.34
1.0
2020-11-15, Close, 16064.02
1.0
2020-11-15, Close, 16041.73
1.0
2020-11-15, Close, 16020.01
1.0
2020-11-15, Close, 15900.01
1.0
2020-11-15, Close, 15916.83
1.0
2020-11-15, Close, 15882.05
1.0
2020-11-15, Close, 15858.88
1.0
2020-11-15, Close, 15856.67
1.0
2020-11-15, Close, 15939.93
1.0
2020-11-15, Close, 15966.89
0.0
2020-11-15, SELL CREATE, 15966.89
2020-11-16, SELL EXECUTED, Price: 15970.00, Cost: 2171383.74, Comm 0.00
2020-11-16, OPERATION PROFIT, GROSS -3851.88, NET 

2020-11-23, Close, 18281.63
1.0
2020-11-23, Close, 18398.05
1.0
2020-11-23, Close, 18358.71
1.0
2020-11-23, Close, 18357.92
1.0
2020-11-23, Close, 18459.89
1.0
2020-11-23, Close, 18397.54
1.0
2020-11-23, Close, 18422.02
1.0
2020-11-23, Close, 18435.56
1.0
2020-11-23, Close, 18384.82
1.0
2020-11-24, Close, 18375.70
1.0
2020-11-24, Close, 18485.11
1.0
2020-11-24, Close, 18360.00
0.0
2020-11-24, SELL CREATE, 18360.00
2020-11-24, SELL EXECUTED, Price: 18360.00, Cost: 2453564.90, Comm 0.00
2020-11-24, OPERATION PROFIT, GROSS -36592.91, NET -36592.91
2020-11-24, Close, 18367.39
1.0
2020-11-24, BUY CREATE, 18367.39
2539302.0869593387 18367.39 18459.226949999997 130.6846158371422
2020-11-24, BUY EXECUTED, Price: 18367.25, Cost: 18367.25, Comm 0.00
2020-11-24, BUY EXECUTED, Price: 18367.25, Cost: 2400317.01, Comm 0.00
2020-11-24, Close, 18462.67
1.0
2020-11-24, Close, 18350.13
0.0
2020-11-24, SELL CREATE, 18350.13
2020-11-24, SELL EXECUTED, Price: 18347.44, Cost: 2418684.26, Comm 0.00
2020-11-2

2020-11-30, BUY EXECUTED, Price: 18202.02, Cost: 18202.02, Comm 0.00
2020-11-30, BUY EXECUTED, Price: 18202.02, Cost: 2300127.12, Comm 0.00
2020-11-30, Close, 18454.01
1.0
2020-11-30, Close, 18501.08
0.0
2020-11-30, SELL CREATE, 18501.08
2020-11-30, SELL EXECUTED, Price: 18501.08, Cost: 2318329.14, Comm 0.00
2020-11-30, OPERATION PROFIT, GROSS 38090.25, NET 38090.25
2020-11-30, Close, 18528.36
0.0
2020-11-30, Close, 18606.02
0.0
2020-11-30, Close, 18542.16
0.0
2020-11-30, Close, 18539.96
1.0
2020-11-30, BUY CREATE, 18539.96
2471385.3038768 18539.96 18632.659799999998 126.00541543097138
2020-11-30, BUY EXECUTED, Price: 18539.95, Cost: 18539.95, Comm 0.00
2020-11-30, BUY EXECUTED, Price: 18539.95, Cost: 2336134.10, Comm 0.00
2020-11-30, Close, 18549.66
1.0
2020-11-30, Close, 18634.68
1.0
2020-11-30, Close, 18477.05
0.0
2020-11-30, SELL CREATE, 18477.05
2020-11-30, SELL EXECUTED, Price: 18477.29, Cost: 2354674.05, Comm 0.00
2020-11-30, OPERATION PROFIT, GROSS -7958.16, NET -7958.16
2020-1

2020-12-09, SELL EXECUTED, Price: 18517.49, Cost: 2535773.56, Comm 0.00
2020-12-09, OPERATION PROFIT, GROSS 45865.15, NET 45865.15
2020-12-09, Close, 18557.47
0.0
2020-12-09, Close, 18546.55
0.0
2020-12-10, Close, 18434.00
1.0
2020-12-10, BUY CREATE, 18434.00
2709205.129079395 18434.0 18526.17 138.92482216375134
2020-12-10, BUY EXECUTED, Price: 18434.01, Cost: 18434.01, Comm 0.00
2020-12-10, BUY EXECUTED, Price: 18434.00, Cost: 2560940.17, Comm 0.00
2020-12-10, Close, 18434.00
1.0
2020-12-10, Close, 18385.11
1.0
2020-12-10, Close, 18410.62
1.0
2020-12-10, Close, 18419.25
1.0
2020-12-10, Close, 18372.25
1.0
2020-12-10, Close, 18303.70
1.0
2020-12-10, Close, 18341.54
1.0
2020-12-10, Close, 18441.75
1.0
2020-12-10, Close, 18238.91
0.0
2020-12-10, SELL CREATE, 18238.91
2020-12-10, SELL EXECUTED, Price: 18238.90, Cost: 2579374.18, Comm 0.00
2020-12-10, OPERATION PROFIT, GROSS -27299.34, NET -27299.34
2020-12-10, Close, 18139.24
1.0
2020-12-10, BUY CREATE, 18139.24
2681905.7862752476 18139.2

1.0
2020-12-19, Close, 22914.23
1.0
2020-12-19, Close, 23074.04
1.0
2020-12-19, Close, 23208.04
1.0
2020-12-19, Close, 23328.01
1.0
2020-12-19, Close, 23591.89
1.0
2020-12-19, Close, 24009.61
0.0
2020-12-19, SELL CREATE, 24009.61
2020-12-19, SELL EXECUTED, Price: 24009.61, Cost: 2996059.93, Comm 0.00
2020-12-19, OPERATION PROFIT, GROSS 133113.89, NET 133113.89
2020-12-19, Close, 23937.40
0.0
2020-12-19, Close, 23866.82
1.0
2020-12-19, BUY CREATE, 23866.82
3278310.749492486 23866.82 23986.154099999996 129.8413742792498
2020-12-19, BUY EXECUTED, Price: 23865.81, Cost: 23865.81, Comm 0.00
2020-12-19, BUY EXECUTED, Price: 23865.81, Cost: 3098769.57, Comm 0.00
2020-12-19, Close, 23838.26
1.0
2020-12-19, Close, 23940.07
1.0
2020-12-19, Close, 23994.59
1.0
2020-12-19, Close, 23942.94
1.0
2020-12-19, Close, 23849.99
1.0
2020-12-20, Close, 23514.75
1.0
2020-12-20, Close, 23509.61
1.0
2020-12-20, Close, 23458.05
1.0
2020-12-20, Close, 23370.01
1.0
2020-12-20, Close, 23460.22
1.0
2020-12-20, Clos

In [124]:
cerebro.plot()

ImportError: cannot import name 'warnings' from 'matplotlib.dates' (/Users/jmcallister/.local/share/virtualenvs/quant-trading-gcHAf6Sx/lib/python3.9/site-packages/matplotlib/dates.py)